In [39]:
import pandas as pd
import numpy as np

from Bio import SeqIO
from Bio import Entrez
from Bio.Alphabet import generic_protein, IUPAC
import math, re
import argparse
import ftplib
import socket
import random
import time
from random import randint
import colorsys
import os, sys, os.path, math
import gzip
import getopt
from collections import OrderedDict
import subprocess
from matplotlib.widgets import CheckButtons
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib as mpl
from matplotlib.pyplot import figure, tight_layout
from collections import Counter 
import ete3

поменять пути к файлам <br>
переименовать переменные

In [ ]:
LengthDict={}

In [7]:
mpl.rcParams['pdf.fonttype'] = 42
mpl.rcParams['ps.fonttype'] = 42
genes_no = 8
x = 8
y = 8

In [69]:
def random_color(h=None):
    """Generates a random color in RGB format."""
    if not h:
        c = int((random.randrange(0,100,5))*3.6)/100
    d = 0.5
    e = 0.5
    return _hls2hex(c, d, e)

def _hls2hex(c, d, e):
    return '#%02x%02x%02x' %tuple(map(lambda f: int(f*255),colorsys.hls_to_rgb(c, d, e)))


def outliner (item):
    if item =='#ffffff':
        return '#bebebe'
    elif item =='#f2f2f2':
        return '#008000'
    elif item =='#f2f2f3':
        return '#000080'
    else:
        return item

In [10]:
familyDict={} # Accession:Assigned family Number from Jackhammer
with open('/home/marfa/Desktop/lab/mycofactocin/mftb/flags/mftb_g8_flankgene.fasta_cluster_out_3_1e-10_clusters.tsv', 'r') as clusterIn:
    for line in clusterIn:
        if line[0]!='#':
            line=line.rstrip().split('\t')
            if int(line[1])>1:
                for item in (line[2].split(';')):
                    familyDict[item]=int(line[0])
            else:
                familyDict[line[2]]=0


In [67]:
familynum=[]
for acc in familyDict:
    familynum.append(familyDict[acc])
    
center=int(max(familynum))+1
noProt=int(max(familynum))+2
noProtP=int(max(familynum))+3
noColor=int(max(familynum))+4

for ids in LengthDict:
    if ids.split('#')[0][-1]=='*':
        if ids.split('#')[0][:2].lower()=='ps':
            familyDict[ids.split('#')[0]]=noProtP
        else:
            familyDict[ids.split('#')[0]]=noProt
    if ids.split('#')[0] not in familyDict:
        if ids in NqueryDict:
            familyDict[ids.split('#')[0]]=center
        else:
            familyDict[ids.split('#')[0]]=noColor

color={}
color[noColor]='#ffffff'
color[center]='#000000'
color[noProt]='#f2f2f2'
color[noProtP]='#f2f2f3'

colorDict={}
for families in set(familynum):
    if families == 0:
        colorDict[families]=str('#ffffff')
    else:
        if random_color()!='#ffffff' or random_color()!='#000000' or random_color()!='#f2f2f2' or random_color()!='#f2f2f3' :
            colorDict[families]=random_color()

colorDict.update(color)

In [92]:
df = pd.read_csv('/home/marfa/Desktop/lab/mycofactocin/mftb/flags/mftb_g8_operon.tsv', sep = '\t', usecols = [0,1,11], header = 0, names = ['prot', 'len','assembl'])

prot = []
length = []
NqueryDict = {}
LengthDict = {}
for k in df['prot']:
    if type(k) == float:
        prot.append(k)
    else:
        prot.append(k.split('|')[0])

df['prot'] = prot

for ind in df.index:
    NqueryDict[df.loc[ind,'prot']] = [df.loc[ind,'assembl']]
    LengthDict[df.loc[ind,'prot']] = [df.loc[ind,'len']]

#del LengthDict[np.nan]
LengthDict

{'WP_011566067.1#1': [453],
 'WP_011940374.1#2': [204],
 'WP_226980745.1#3': [204],
 'WP_015759610.1#4': [1641],
 'WP_015746104.1#5': [786],
 'WP_012852712.1#6': [1068],
 'WP_012873300.1#7': [804],
 'WP_012950891.1#8': [543],
 'WP_041451260.1#9': [264],
 'WP_013809152.1#10': [1140],
 'WP_013873929.1#11': [1035],
 'WP_014378467.1#12': [228],
 'WP_014442838.1#13': [1470],
 'WP_014814231.1#14': [1248],
 'WP_015305006.1#15': [1254],
 'WP_015443073.1#16': [744],
 'WP_006541655.1#17': [834],
 'WP_009680802.1#18': [1257],
 'WP_194624246.1#19': [1263],
 'WP_003923362.1#20': [1251],
 'WP_009476072.1#21': [558],
 'WP_202948845.1#22': [1536],
 'WP_017593158.1#23': [885],
 'WP_143528577.1#24': [453],
 'WP_098002455.1#25': [1263],
 'WP_163664222.1#26': [1254],
 'WP_163779744.1#27': [1641],
 'WP_085258087.1#28': [564],
 'WP_083045943.1#29': [663],
 'WP_085157628.1#30': [990],
 'WP_197910665.1#31': [1251],
 'WP_197939601.1#32': [1251],
 'WP_163801650.1#33': [1251],
 'WP_197931663.1#34': [1578],
 'WP_

In [89]:
 
# 1. Data File input
arrowList = []
domainList = []
accession_List = []


# 2. Drawing the plots
fig, ax = plt.subplots(1, 2, sharey = 'row', figsize=(x, y), gridspec_kw={'width_ratios': [5, 15]})


# 3. Operon (main) file input 
main_file = open('/home/marfa/Desktop/lab/mycofactocin/mftb/flags/mftb_g8_operon.tsv','r').read()
eg1 = main_file.split("\n\n\n\n") #разделение по query
y_level_m = 0
for m in eg1:
    if m != '':
        row = 0
        entries1 = m.splitlines() #each prot for query
        ndoms=len(entries1) #number of domains in cluster
        y_level_m = y_level_m - 2.75 #-round(postscriptSize(newQ))
        for entry in entries1:
            items1 = entry.split("\t")
            x_gene_start = int(items1[5])
            x_gene_end = int(items1[6])
            dx_gene_length = int(items1[1])
            gene_direction = items1[3]
            dom1_name = int(items1[4])
            id1 = str(items1[9])
            accession = str(items1[0])
            accession_List.append(accession)

            # 3a. When genes are to small the arrow shape is distorted because the coordinates are too close to each other.
            #This makes these genes longer to keep the shape of the arrow. 
            if dx_gene_length < 100:
                dx_gene_length = int(items1[1]) * 2.5
            else:
                dx_gene_length = int(items1[1])

            # 3b. Gene diretion and the pointing the arrow head in the correct direction
            if gene_direction == '-':
                x_gene_start = int(items1[6]) #разворот координат
                x_gene_end = int(items1[5])
                dx_gene_length = dx_gene_length*(-1)
            else:
                x_gene_start = int(items1[5])
                x_gene_end = int(items1[6])
                dx_gene_length = dx_gene_length

            # 3c. Drawing the genes as arrows. 
            if abs(dx_gene_length) < 200:
                arrowList.append(ax[1].arrow(x=x_gene_start, 
                                             y = y_level_m * 0.65, 
                                             dx = dx_gene_length, 
                                             dy = 0, width = 1.1, head_width=2*1.1, 
                                             length_includes_head = True, 
                                             head_length = abs(dx_gene_length) / 2, 
                                             facecolor = colorDict[dom1_name], 
                                             edgecolor = outliner(colorDict[dom1_name]), alpha = 1))               
            else:
                arrowList.append(ax[1].arrow(x=x_gene_start, 
                                             y = y_level_m * 0.65, 
                                             dx=dx_gene_length, 
                                             dy=0, width=1.1, head_width=1.1, 
                                             length_includes_head = True, 
                                             head_length = 150, 
                                             facecolor = colorDict[dom1_name], 
                                             edgecolor = outliner(colorDict[dom1_name]), alpha=1))

            # 5. Adding the family number inside the gene/arrow
            text_x = x_gene_start + (dx_gene_length / 2) #position of the text in arrow

            if (dom1_name != 0) and ('pseudogene_' not in id1) and ('RNA_' not in id1) and ('other' not in id1) and (x_gene_start != 1):
                ax[1].text(text_x, 
                           y_level_m * 0.65 - 0.35, 
                           s = dom1_name, 
                           horizontalalignment='center', color = 'k', 
                           font = {'family' : 'sans-serif','size'   : 8})
            else:
                pass

            # 6. Adding the second plot (left-hand side) with the organism name and accesion nr etc. 
            ptnstats = entries1[0].split("\t")
            org = ptnstats[0][:ptnstats[0].index('|')] + ptnstats[0][ptnstats[0].index('|'):].replace('_',' ')
            ax[0].text(0.5, 
                       y_level_m * 0.65 - 0.35, 
                       org, horizontalalignment='center', 
                       color = '#000000', 
                       font = {'family' : 'sans-serif','size':10})
            ax[0].set_axis_off()

            row = row + 1

            
y_new = ((len(Counter(accession_List).keys())) * 0.5)
x_new = 150
fig.set_figheight(y_new)
fig.set_figwidth(x_new)
#plt.tight_layout()
plt.axis('off')
plt.savefig('/home/marfa/Desktop/lab/mycofactocin/mftb/flags/mftb_g8_operon_150.pdf', format='pdf', bbox_inches='tight') #For FlaGs input

